In [1]:
import pandas as pd
import numpy as np
from rdkit import Chem
from rdkit.Chem import AllChem
import chemprop

In [2]:
import sys
sys.path.append('../../../../code')

from metrics import get_hi_metrics
from utils import chemprop_prepare_df, chemprop_process_folder

Skipped loading some Tensorflow models, missing a dependency. No module named 'tensorflow'
Skipped loading modules with pytorch-geometric dependency, missing a dependency. No module named 'torch_geometric'
Skipped loading modules with pytorch-geometric dependency, missing a dependency. cannot import name 'DMPNN' from 'deepchem.models.torch_models' (/home/steshin/miniconda3/envs/lohi_benchmark/lib/python3.10/site-packages/deepchem/models/torch_models/__init__.py)
Skipped loading some Jax models, missing a dependency. No module named 'jax'


In [3]:
train = pd.read_csv('../../../../data/hi/hiv/train_1.csv')
test = pd.read_csv('../../../../data/hi/hiv/test_1.csv')

train

Unnamed: 0                                             smiles  value
0               4                             O=S(=O)(O)CCS(=O)(=O)O      0
1              21                                  CC(C)CCS(=O)(=O)O      0
2              90                                      O=S(=O)(O)CCO      0
3             106                                       O=S(=O)(O)CO      0
4             117                                   O=S(=O)(O)CCCCBr      0
...           ...                                                ...    ...
15691       40932  COC(=O)c1cc2cc3c(c(O)c2c(=O)o1)OC1(Oc2c(O)c4c(...      0
15692       40973          CCCCC1C(OCOc2ccccc2)COC(=O)N1C(C)c1ccccc1      0
15693       41024    CC(C)=CC1CC(C)C2CCC(C)C3C(=O)C(O)=C(C)C(=O)C123      0
15694       41026             CCOC(=O)C12C(=O)C(C)CCC1C(C)CC2C=C(C)C      0
15695       41106  Cc1ccc(C=C2CN(C)CC3C(c4ccc(C)cc4)=C(C#N)C(=O)N...      0

[15696 rows x 3 columns]

In [4]:
import os
import os
import shutil

temp_datapath = '/tmp/chemprop/'
if os.path.exists(temp_datapath) and os.path.isdir(temp_datapath):
    shutil.rmtree(temp_datapath)
os.mkdir(temp_datapath)

input_paths = [
    '/data/steshin/gero_benchmark/data/hi/hiv/'
]

output_paths = [
    temp_datapath
]

for i in range(len(input_paths)):
    chemprop_process_folder(input_paths[i], output_paths[i])

In [5]:
base_arguments = [
    '--dataset_type', 'classification', 
    '--data_path', temp_datapath + 'train_1.csv',
    '--separate_val_path', temp_datapath + 'test_1.csv',
    '--separate_test_path', temp_datapath + 'test_1.csv',
    '--save_preds',
    '--metric', 'prc-auc',
    '--epochs', '70',
    '--gpu', '1',
    '--save_dir', temp_datapath + 'checkpoint',
    '--features_generator', 'rdkit_2d_normalized',
    '--no_features_scaling',
]

In [6]:
param_dict = {
    '--depth': ['3', '4', '5', '6'],
    '--dropout': ['0.0', '0.2', '0.3', '0.5', '0.7'],
    '--ffn_hidden_size': ['600', '1200', '2400', '3600'],
    '--ffn_num_layers': ['1', '2', '3'],
    '--hidden_size': ['600', '1200', '2400', '3600']
}

In [7]:
from copy import copy
from tqdm import tqdm
import pickle
from sklearn.model_selection import ParameterSampler

hyperparam_list = list(ParameterSampler(param_dict, n_iter=20))

best_score = 0.0
best_hyperparams = None

for i, hyperparam in tqdm(enumerate(hyperparam_list)):
    print('HYPERPARAMETER', i)
    print(hyperparam)
    result_arguments = copy(base_arguments)
    for key, value in hyperparam.items():
        result_arguments.append(key)
        result_arguments.append(value)
    # Train
    args = chemprop.args.TrainArgs().parse_args(result_arguments)
    mean_score, std_score = chemprop.train.cross_validate(args=args, train_func=chemprop.train.run_training)

    test_preds = pd.read_csv(temp_datapath + 'checkpoint/test_preds.csv')
    metrics = get_hi_metrics(test, test_preds['targets'].to_list())

    score = metrics['prc_auc']
    if score > best_score:
        print('New best PRC AUC:', score)
        best_score = score
        best_hyperparams = hyperparam

0it [00:00, ?it/s]Command line
python /home/steshin/miniconda3/envs/lohi_benchmark/lib/python3.10/site-packages/ipykernel_launcher.py --ip=127.0.0.1 --stdin=9003 --control=9001 --hb=9000 --Session.signature_scheme="hmac-sha256" --Session.key=b"c668f21c-dacd-4f5f-8aa9-94620e06a849" --shell=9002 --transport="tcp" --iopub=9004 --f=/home/steshin/.local/share/jupyter/runtime/kernel-v2-11059562ZE03qG2AyOv.json
Args
{'activation': 'ReLU',
 'adding_h': False,
 'aggregation': 'mean',
 'aggregation_norm': 100,
 'atom_descriptor_scaling': True,
 'atom_descriptors': None,
 'atom_descriptors_path': None,
 'atom_descriptors_size': 0,
 'atom_features_size': 0,
 'atom_messages': False,
 'batch_size': 50,
 'bias': False,
 'bias_solvent': False,
 'bond_feature_scaling': True,
 'bond_features_path': None,
 'bond_features_size': 0,
 'cache_cutoff': 10000,
 'checkpoint_dir': None,
 'checkpoint_frzn': None,
 'checkpoint_path': None,
 'checkpoint_paths': None,
 'class_balance': False,
 'config_path': None,
 

HYPERPARAMETER 0
{'--hidden_size': '600', '--ffn_num_layers': '3', '--ffn_hidden_size': '3600', '--dropout': '0.3', '--depth': '5'}


Setting molecule featurization parameters to default.
Loading data
15696it [00:00, 397451.07it/s]
[17:25:19] WARNING: not removing hydrogen atom without neighbors
[17:25:19] WARNING: not removing hydrogen atom without neighbors
[17:25:19] WARNING: not removing hydrogen atom without neighbors
[17:25:19] WARNING: not removing hydrogen atom without neighbors
[17:25:19] WARNING: not removing hydrogen atom without neighbors
[17:25:19] WARNING: not removing hydrogen atom without neighbors
100%|██████████| 15696/15696 [00:00<00:00, 169197.23it/s]
Number of tasks = 1
Fold 0
Splitting data with seed 0
7847it [00:00, 48623.56it/s]
100%|██████████| 7847/7847 [00:00<00:00, 171566.88it/s]
7847it [00:00, 452906.34it/s]
100%|██████████| 7847/7847 [00:00<00:00, 167134.89it/s]
Class sizes
targets 0: 96.18%, 1: 3.82%
Total size = 15,696 | train size = 15,696 | val size = 7,847 | test size = 7,847
Building model 0
MoleculeModel(
  (sigmoid): Sigmoid()
  (encoder): MPN(
    (encoder): ModuleList(
      (0

New best PRC AUC: 0.3161452873268859
HYPERPARAMETER 1
{'--hidden_size': '600', '--ffn_num_layers': '3', '--ffn_hidden_size': '2400', '--dropout': '0.3', '--depth': '5'}


Setting molecule featurization parameters to default.
Loading data
15696it [00:00, 274242.35it/s]
[18:08:02] WARNING: not removing hydrogen atom without neighbors
[18:08:02] WARNING: not removing hydrogen atom without neighbors
[18:08:02] WARNING: not removing hydrogen atom without neighbors
[18:08:02] WARNING: not removing hydrogen atom without neighbors
100%|██████████| 15696/15696 [00:00<00:00, 106095.93it/s]
Number of tasks = 1
Fold 0
Splitting data with seed 0
7847it [00:00, 294610.47it/s]
100%|██████████| 7847/7847 [00:00<00:00, 158577.99it/s]
7847it [00:00, 426695.15it/s]
100%|██████████| 7847/7847 [00:00<00:00, 159840.24it/s]
Class sizes
targets 0: 96.18%, 1: 3.82%
Total size = 15,696 | train size = 15,696 | val size = 7,847 | test size = 7,847
Building model 0
MoleculeModel(
  (sigmoid): Sigmoid()
  (encoder): MPN(
    (encoder): ModuleList(
      (0): MPNEncoder(
        (dropout_layer): Dropout(p=0.3, inplace=False)
        (act_func): ReLU()
        (W_i): Linear(in_feature

...

15696it [00:00, 98060.35it/s]
[08:34:57] WARNING: not removing hydrogen atom without neighbors
[08:34:57] WARNING: not removing hydrogen atom without neighbors
[08:34:57] WARNING: not removing hydrogen atom without neighbors
[08:34:57] WARNING: not removing hydrogen atom without neighbors
100%|██████████| 15696/15696 [00:00<00:00, 157880.87it/s]
Number of tasks = 1
Fold 0
Splitting data with seed 0
7847it [00:00, 48071.32it/s]
100%|██████████| 7847/7847 [00:00<00:00, 165450.33it/s]
7847it [00:00, 456841.70it/s]
100%|██████████| 7847/7847 [00:00<00:00, 170428.83it/s]
Class sizes
targets 0: 96.18%, 1: 3.82%
Total size = 15,696 | train size = 15,696 | val size = 7,847 | test size = 7,847
Building model 0
MoleculeModel(
  (sigmoid): Sigmoid()
  (encoder): MPN(
    (encoder): ModuleList(
      (0): MPNEncoder(
        (dropout_layer): Dropout(p=0.2, inplace=False)
        (act_func): ReLU()
        (W_i): Linear(in_features=147, out_features=600, bias=False)
        (W_h): Linear(in_feature

HYPERPARAMETER 18
{'--hidden_size': '2400', '--ffn_num_layers': '3', '--ffn_hidden_size': '600', '--dropout': '0.3', '--depth': '6'}


15696it [00:00, 99852.57it/s]
[09:08:33] WARNING: not removing hydrogen atom without neighbors
[09:08:33] WARNING: not removing hydrogen atom without neighbors
[09:08:33] WARNING: not removing hydrogen atom without neighbors
[09:08:33] WARNING: not removing hydrogen atom without neighbors
100%|██████████| 15696/15696 [00:00<00:00, 166410.01it/s]
Number of tasks = 1
Fold 0
Splitting data with seed 0
7847it [00:00, 48572.18it/s]
100%|██████████| 7847/7847 [00:00<00:00, 164311.30it/s]
7847it [00:00, 445917.21it/s]
100%|██████████| 7847/7847 [00:00<00:00, 166233.33it/s]
Class sizes
targets 0: 96.18%, 1: 3.82%
Total size = 15,696 | train size = 15,696 | val size = 7,847 | test size = 7,847
Building model 0
MoleculeModel(
  (sigmoid): Sigmoid()
  (encoder): MPN(
    (encoder): ModuleList(
      (0): MPNEncoder(
        (dropout_layer): Dropout(p=0.3, inplace=False)
        (act_func): ReLU()
        (W_i): Linear(in_features=147, out_features=2400, bias=False)
        (W_h): Linear(in_featur

HYPERPARAMETER 19
{'--hidden_size': '1200', '--ffn_num_layers': '2', '--ffn_hidden_size': '3600', '--dropout': '0.2', '--depth': '6'}


15696it [00:00, 387700.06it/s]
[10:15:06] WARNING: not removing hydrogen atom without neighbors
[10:15:06] WARNING: not removing hydrogen atom without neighbors
[10:15:06] WARNING: not removing hydrogen atom without neighbors
[10:15:06] WARNING: not removing hydrogen atom without neighbors
100%|██████████| 15696/15696 [00:00<00:00, 164940.35it/s]
Number of tasks = 1
Fold 0
Splitting data with seed 0
7847it [00:00, 451118.50it/s]
100%|██████████| 7847/7847 [00:00<00:00, 165665.19it/s]
7847it [00:00, 462146.73it/s]
100%|██████████| 7847/7847 [00:00<00:00, 163834.45it/s]
Class sizes
targets 0: 96.18%, 1: 3.82%
Total size = 15,696 | train size = 15,696 | val size = 7,847 | test size = 7,847
Building model 0
MoleculeModel(
  (sigmoid): Sigmoid()
  (encoder): MPN(
    (encoder): ModuleList(
      (0): MPNEncoder(
        (dropout_layer): Dropout(p=0.2, inplace=False)
        (act_func): ReLU()
        (W_i): Linear(in_features=147, out_features=1200, bias=False)
        (W_h): Linear(in_feat

In [10]:
print(best_hyperparams)


{'--hidden_size': '3600', '--ffn_num_layers': '2', '--ffn_hidden_size': '3600', '--dropout': '0.2', '--depth': '6'}


In [11]:
print(best_score)

0.3700800255854764


In [12]:
from copy import copy

result_arguments = copy(base_arguments)
result_arguments.extend([
    '--hidden_size', '3600',
    '--ffn_num_layers', '2',
    '--ffn_hidden_size', '3600',
    '--dropout', '0.2',
    '--depth', '6'
])

args = chemprop.args.TrainArgs().parse_args(result_arguments)
mean_score, std_score = chemprop.train.cross_validate(args=args, train_func=chemprop.train.run_training)


Command line
python /home/steshin/miniconda3/envs/lohi_benchmark/lib/python3.10/site-packages/ipykernel_launcher.py --ip=127.0.0.1 --stdin=9003 --control=9001 --hb=9000 --Session.signature_scheme="hmac-sha256" --Session.key=b"c668f21c-dacd-4f5f-8aa9-94620e06a849" --shell=9002 --transport="tcp" --iopub=9004 --f=/home/steshin/.local/share/jupyter/runtime/kernel-v2-11059562ZE03qG2AyOv.json
Args
{'activation': 'ReLU',
 'adding_h': False,
 'aggregation': 'mean',
 'aggregation_norm': 100,
 'atom_descriptor_scaling': True,
 'atom_descriptors': None,
 'atom_descriptors_path': None,
 'atom_descriptors_size': 0,
 'atom_features_size': 0,
 'atom_messages': False,
 'batch_size': 50,
 'bias': False,
 'bias_solvent': False,
 'bond_feature_scaling': True,
 'bond_features_path': None,
 'bond_features_size': 0,
 'cache_cutoff': 10000,
 'checkpoint_dir': None,
 'checkpoint_frzn': None,
 'checkpoint_path': None,
 'checkpoint_paths': None,
 'class_balance': False,
 'config_path': None,
 'crossval_index_di

KeyboardInterrupt: 

In [7]:
best_epoch = 40

In [24]:
test_result

Unnamed: 0                                             smiles  value  \
0            383   CC(C)Oc1ccccc1N1CCN(Cc2cccc(C(=O)N3CCCCC3)c2)CC1   True   
1            386     CC(C)Oc1ccccc1N1CCN(Cc2cccc(CN3CCCCC3=O)c2)CC1   True   
2            389       CC(C)Oc1ccccc1N1CCN(Cc2ccccc2CN2CCCCC2=O)CC1   True   
3           2695  COc1ccccc1N1CCN(CC2COCC(c3ccccc3)(c3ccccc3)O2)CC1   True   
4           2995  COc1ccccc1N1CCN(C[C@H]2OCCOC2(c2ccccc2)c2ccccc...  False   
...          ...                                                ...    ...   
1186        5766          O=S(=O)(c1ccccc1)c1cnc2c(N3CCNCC3)cccc2c1   True   
1187        6025  O[C@H]1[C@@H](NC[C@@H]2COc3ccccc3O2)CC[C@@H]1O...  False   
1188        6018  O[C@@H]1[C@H](NC[C@@H]2COc3ccccc3O2)CC[C@H]1Oc...  False   
1189        6019  O[C@@H]1[C@H](NC[C@H]2COc3ccccc3O2)CC[C@H]1Oc1...  False   
1190        6026  O[C@H]1[C@@H](NC[C@H]2COc3ccccc3O2)CC[C@@H]1Oc...  False   

         preds  
0     0.148691  
1     0.137544  
2     0.049242  
3     0.029785  
4     0.523535  
...        ...  
1186  0.073102  
1187  0.044055  
1188  0.737260  
1189  0.058900  
1190       NaN  

[1191 rows x 4 columns]

In [23]:
test

Unnamed: 0                                             smiles  value
0            383   CC(C)Oc1ccccc1N1CCN(Cc2cccc(C(=O)N3CCCCC3)c2)CC1   True
1            386     CC(C)Oc1ccccc1N1CCN(Cc2cccc(CN3CCCCC3=O)c2)CC1   True
2            389       CC(C)Oc1ccccc1N1CCN(Cc2ccccc2CN2CCCCC2=O)CC1   True
3           2695  COc1ccccc1N1CCN(CC2COCC(c3ccccc3)(c3ccccc3)O2)CC1   True
4           2995  COc1ccccc1N1CCN(C[C@H]2OCCOC2(c2ccccc2)c2ccccc...  False
...          ...                                                ...    ...
1186        5766          O=S(=O)(c1ccccc1)c1cnc2c(N3CCNCC3)cccc2c1   True
1187        6025  O[C@H]1[C@@H](NC[C@@H]2COc3ccccc3O2)CC[C@@H]1O...  False
1188        6018  O[C@@H]1[C@H](NC[C@@H]2COc3ccccc3O2)CC[C@H]1Oc...  False
1189        6019  O[C@@H]1[C@H](NC[C@H]2COc3ccccc3O2)CC[C@H]1Oc1...  False
1190        6026  O[C@H]1[C@@H](NC[C@H]2COc3ccccc3O2)CC[C@@H]1Oc...  False

[1191 rows x 3 columns]